# County Source Data

Using Pandas to import csv file of Zipcodes to identify counties associated with cities in the Instacart dataset.  

The reason for this is that the Food Desert data is based on county level information and the only way to compare the areas is to utilize the data set and join in MongoDB.

### Import dependencies

In [1]:
import os
import pandas as pd
from pandas import DataFrame
import pymongo

### Setup DB connection and establish collection for storage

In [2]:
# Setup connection to MongoDB
conn = 'mongodb://localhost:27017'
client = pymongo.MongoClient(conn)

In [3]:
# Create Collection to receive data
db = client.food_desert_db
db.zipcode_county_data.drop()
collection = db.zipcode_county_data

### Import and read file

Bringing in path for datafile as well as reference file of states for Instacart Service area

In [11]:
csv_path = os.path.join('Data', 'zip_code_database.csv')
states_path = os.path.join('Data','instacart_states.csv')

In [17]:
states = pd.read_csv(states_path)
states.head()

Unnamed: 0 state  counts
0           0    NY     851
1           1    PA     850
2           2    CA     704
3           3    TX     524
4           4    OH     513

In [16]:
pd.read_csv(states_path, nrows=1).columns

Index(['Unnamed: 0', 'state', 'counts'], dtype='object')

In [5]:
pd.read_csv(csv_path, nrows=1).columns

Index(['zip', 'type', 'decommissioned', 'primary_city', 'acceptable_cities',
       'unacceptable_cities', 'state', 'county', 'timezone', 'area_codes',
       'world_region', 'country', 'latitude', 'longitude',
       'irs_estimated_population_2015'],
      dtype='object')

In [20]:
data = pd.read_csv(csv_path)[['primary_city', 'acceptable_cities','state', 'county']]
data.head(10)

primary_city acceptable_cities state               county
0   Holtsville               NaN    NY              Suffolk
1   Holtsville               NaN    NY              Suffolk
2     Adjuntas               NaN    PR   Adjuntas Municipio
3       Aguada               NaN    PR     Aguada Municipio
4    Aguadilla             Ramey    PR  Aguadilla Municipio
5    Aguadilla             Ramey    PR                  NaN
6    Aguadilla               NaN    PR                  NaN
7      Maricao               NaN    PR    Maricao Municipio
8       Anasco               NaN    PR     Anasco Municipio
9      Angeles               NaN    PR                  NaN

In [21]:
data.count()

primary_city         42632
acceptable_cities     9023
state                42632
county               41790
dtype: int64

In [22]:
data.loc[data.isnull().any(axis=1)]

primary_city acceptable_cities state  \
0         Holtsville               NaN    NY   
1         Holtsville               NaN    NY   
2           Adjuntas               NaN    PR   
3             Aguada               NaN    PR   
5          Aguadilla             Ramey    PR   
6          Aguadilla               NaN    PR   
7            Maricao               NaN    PR   
8             Anasco               NaN    PR   
9            Angeles               NaN    PR   
10           Arecibo               NaN    PR   
11           Arecibo               NaN    PR   
12           Arecibo               NaN    PR   
13          Bajadero               NaN    PR   
14       Barceloneta               NaN    PR   
15          Boqueron               NaN    PR   
16         Cabo Rojo               NaN    PR   
17          Penuelas               NaN    PR   
18             Camuy               NaN    PR   
20           Rosario               NaN    PR   
21     Sabana Grande               NaN    PR   
22            Ciales               NaN    PR   
23            Utuado               NaN    PR   
24            Dorado               NaN    PR   
25          Ensenada               NaN    PR   
26           Florida               NaN    PR   
27       Garrochales               NaN    PR   
28           Guanica               NaN    PR   
29        Guayanilla               NaN    PR   
30           Hatillo               NaN    PR   
31       Hormigueros               NaN    PR   
...              ...               ...   ...   
42586         Teller               NaN    AK   
42587            Tok               NaN    AK   
42589        Venetie               NaN    AK   
42590     Wainwright               NaN    AK   
42591          Wales               NaN    AK   
42594         Ambler               NaN    AK   
42597      Fairbanks               NaN    AK   
42599         Juneau               NaN    AK   
42600         Juneau               NaN    AK   
42601         Juneau               NaN    AK   
42602         Juneau               NaN    AK   
42603         Juneau               NaN    AK   
42604         Angoon               NaN    AK   
42607     Elfin Cove               NaN    AK   
42608       Gustavus               NaN    AK   
42609         Haines               NaN    AK   
42610         Hoonah               NaN    AK   
42611           Kake               NaN    AK   
42612        Pelican               NaN    AK   
42614          Sitka               NaN    AK   
42616        Skagway               NaN    AK   
42618         Juneau               NaN    AK   
42623          Craig               NaN    AK   
42624       Hydaburg               NaN    AK   
42625          Hyder               NaN    AK   
42626        Klawock               NaN    AK   
42627     Metlakatla               NaN    AK   
42628    Point Baker               NaN    AK   
42629      Ward Cove               NaN    AK   
42630       Wrangell               NaN    AK   

                                        county  
0                                      Suffolk  
1                                      Suffolk  
2                           Adjuntas Municipio  
3                             Aguada Municipio  
5                                          NaN  
6                                          NaN  
7                            Maricao Municipio  
8                             Anasco Municipio  
9                                          NaN  
10                           Arecibo Municipio  
11                                         NaN  
12                                         NaN  
13                           Arecibo Municipio  
14                       Barceloneta Municipio  
15                         Cabo Rojo Municipio  
16                         Cabo Rojo Municipio  
17                          Penuelas Municipio  
18                             Camuy Municipio  
20                                         NaN  
21                     Sabana Grande Municipio  
22

In [23]:
data.dropna(subset=['county'], inplace=True)

In [24]:
#data.drop(data.loc[data['state']=="PR"].index, inplace=True)
data = data[data['state'].isin(states['state'])]

In [25]:
data['acceptable_cities'].fillna(data['primary_city'],inplace=True)
data.head()

primary_city acceptable_cities state     county
0     Holtsville        Holtsville    NY    Suffolk
1     Holtsville        Holtsville    NY    Suffolk
194       Agawam            Agawam    MA    Hampden
195      Amherst   Cushman, Pelham    MA  Hampshire
196      Amherst           Amherst    MA  Hampshire

In [26]:
data_duplicates_removed = DataFrame.drop_duplicates(data).copy()
data_duplicates_removed.count()

primary_city         31912
acceptable_cities    31912
state                31912
county               31912
dtype: int64

In [27]:
data_duplicates_removed.head()

primary_city acceptable_cities state     county
0     Holtsville        Holtsville    NY    Suffolk
194       Agawam            Agawam    MA    Hampden
195      Amherst   Cushman, Pelham    MA  Hampshire
196      Amherst           Amherst    MA  Hampshire
198        Barre             Barre    MA  Worcester

### Add column to insert city, state so that it can be used to match up with the instacart data and drop unnecessary columns

In [28]:
data_duplicates_removed['primary_city-state'] = data_duplicates_removed['primary_city'] +', '+ data_duplicates_removed['state']
data_duplicates_removed['acceptable_city-state'] = data_duplicates_removed['acceptable_cities'] +', '+ data_duplicates_removed['state']
data_duplicates_removed['primary_city-state/county'] = data_duplicates_removed['primary_city'] +', '+ data_duplicates_removed['state'] +'/'+ data_duplicates_removed['county']
data_duplicates_removed['acceptable_city-state/county'] = data_duplicates_removed['acceptable_cities'] +', '+ data_duplicates_removed['state'] +'/'+ data_duplicates_removed['county']
data_duplicates_removed.head(10)

primary_city acceptable_cities state     county primary_city-state  \
0     Holtsville        Holtsville    NY    Suffolk     Holtsville, NY   
194       Agawam            Agawam    MA    Hampden         Agawam, MA   
195      Amherst   Cushman, Pelham    MA  Hampshire        Amherst, MA   
196      Amherst           Amherst    MA  Hampshire        Amherst, MA   
198        Barre             Barre    MA  Worcester          Barre, MA   
199  Belchertown       Belchertown    MA  Hampshire    Belchertown, MA   
200    Blandford         Blandford    MA    Hampden      Blandford, MA   
201   Bondsville        Bondsville    MA    Hampden     Bondsville, MA   
202    Brimfield         Brimfield    MA    Hampden      Brimfield, MA   
203      Chester           Chester    MA    Hampden        Chester, MA   

    acceptable_city-state  primary_city-state/county  \
0          Holtsville, NY     Holtsville, NY/Suffolk   
194            Agawam, MA         Agawam, MA/Hampden   
195   Cushman, Pelham, MA      Amherst, MA/Hampshire   
196           Amherst, MA      Amherst, MA/Hampshire   
198             Barre, MA        Barre, MA/Worcester   
199       Belchertown, MA  Belchertown, MA/Hampshire   
200         Blandford, MA      Blandford, MA/Hampden   
201        Bondsville, MA     Bondsville, MA/Hampden   
202         Brimfield, MA      Brimfield, MA/Hampden   
203           Chester, MA        Chester, MA/Hampden   

      acceptable_city-state/county  
0           Holtsville, NY/Suffolk  
194             Agawam, MA/Hampden  
195  Cushman, Pelham, MA/Hampshire  
196          Amherst, MA/Hampshire  
198            Barre, MA/Worcester  
199      Belchertown, MA/Hampshire  
200          Blandford, MA/Hampden  
201         Bondsville, MA/Hampden  
202          Brimfield, MA/Hampden  
203            Chester, MA/Hampden

In [29]:
data_duplicates_removed['primary_city-state/county'].value_counts()

Pittsburgh, PA/Allegheny                 41
Miami, FL/Miami-Dade                     35
Cincinnati, OH/Hamilton                  32
Los Angeles, CA/Los Angeles              29
Louisville, KY/Jefferson                 26
Fort Lauderdale, FL/Broward              22
Saint Louis, MO/St. Louis                21
Minneapolis, MN/Hennepin                 20
Cleveland, OH/Cuyahoga                   20
Indianapolis, IN/Marion                  19
Salt Lake City, UT/Salt Lake             18
San Antonio, TX/Bexar                    17
Birmingham, AL/Jefferson                 17
New York, NY/New York                    16
Tampa, FL/Hillsborough                   15
Orlando, FL/Orange                       15
Fort Worth, TX/Tarrant                   15
Buffalo, NY/Erie                         15
Milwaukee, WI/Milwaukee                  14
Dayton, OH/Montgomery                    14
Seattle, WA/King                         13
Saint Petersburg, FL/Pinellas            13
Atlanta, GA/Fulton              

In [30]:
data_duplicates_removed['acceptable_city-state/county'].value_counts()

Flushing, NY/Queens                                                                                               12
Boston, MA/Suffolk                                                                                                11
Baltimore, MD/Baltimore                                                                                           11
Cleveland, OH/Cuyahoga                                                                                            10
Jamaica, NY/Queens                                                                                                10
Detroit, MI/Wayne                                                                                                  7
Richmond, RI/Washington                                                                                            6
Gallup, NM/McKinley                                                                                                6
Kingman, AZ/Mohave                                              

In [32]:
primary_cities = data_duplicates_removed[['primary_city-state/county']]
primary_cities.rename(columns = {'primary_city-state/county': 'city-state/county'}, 
                                 inplace = True) 
primary_cities.head()

city-state/county
0    Holtsville, NY/Suffolk
194      Agawam, MA/Hampden
195   Amherst, MA/Hampshire
196   Amherst, MA/Hampshire
198     Barre, MA/Worcester

In [33]:
acceptable_cities = data_duplicates_removed[['acceptable_city-state/county']]
acceptable_cities.rename(columns = {'acceptable_city-state/county': 'city-state/county'}, 
                                 inplace = True) 
acceptable_cities.head()

city-state/county
0           Holtsville, NY/Suffolk
194             Agawam, MA/Hampden
195  Cushman, Pelham, MA/Hampshire
196          Amherst, MA/Hampshire
198            Barre, MA/Worcester

In [34]:
all_cities = pd.merge(primary_cities, acceptable_cities, on='city-state/county', how='outer')
all_cities.head()

city-state/county
0  Holtsville, NY/Suffolk
1      Agawam, MA/Hampden
2   Amherst, MA/Hampshire
3   Amherst, MA/Hampshire
4   Amherst, MA/Hampshire

In [35]:
all_cities.count()

city-state/county    40503
dtype: int64

In [36]:
all_cities[['city-state','county']] = all_cities['city-state/county'].str.split('/', n=1, expand=True)
all_cities.head()

city-state/county      city-state     county
0  Holtsville, NY/Suffolk  Holtsville, NY    Suffolk
1      Agawam, MA/Hampden      Agawam, MA    Hampden
2   Amherst, MA/Hampshire     Amherst, MA  Hampshire
3   Amherst, MA/Hampshire     Amherst, MA  Hampshire
4   Amherst, MA/Hampshire     Amherst, MA  Hampshire

In [37]:
collection.insert_many(all_cities.to_dict('records'))

In [38]:
listings = db.zipcode_county_data.find()

for listing in listings:
    print(listing)

{'_id': ObjectId('5e1a2fff0fa58fe64d042888'), 'city-state/county': 'Holtsville, NY/Suffolk', 'city-state': 'Holtsville, NY', 'county': 'Suffolk'}
{'_id': ObjectId('5e1a2fff0fa58fe64d042889'), 'city-state/county': 'Agawam, MA/Hampden', 'city-state': 'Agawam, MA', 'county': 'Hampden'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04288a'), 'city-state/county': 'Amherst, MA/Hampshire', 'city-state': 'Amherst, MA', 'county': 'Hampshire'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04288b'), 'city-state/county': 'Amherst, MA/Hampshire', 'city-state': 'Amherst, MA', 'county': 'Hampshire'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04288c'), 'city-state/county': 'Amherst, MA/Hampshire', 'city-state': 'Amherst, MA', 'county': 'Hampshire'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04288d'), 'city-state/county': 'Amherst, MA/Hampshire', 'city-state': 'Amherst, MA', 'county': 'Hampshire'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04288e'), 'city-state/county': 'Barre, MA/Worcester', 'city-state': 'Barre, MA', 'county': 'Worcester'}


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'_id': ObjectId('5e1a2fff0fa58fe64d04a7e5'), 'city-state/county': 'Midland, OR/Klamath', 'city-state': 'Midland, OR', 'county': 'Klamath'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04a7e6'), 'city-state/county': 'New Pine Creek, OR/Modoc', 'city-state': 'New Pine Creek, OR', 'county': 'Modoc'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04a7e7'), 'city-state/county': 'Paisley, OR/Lake', 'city-state': 'Paisley, OR', 'county': 'Lake'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04a7e8'), 'city-state/county': 'Plush, OR/Lake', 'city-state': 'Plush, OR', 'county': 'Lake'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04a7e9'), 'city-state/county': 'Silver Lake, OR/Lake', 'city-state': 'Silver Lake, OR', 'county': 'Lake'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04a7ea'), 'city-state/county': 'Sprague River, OR/Klamath', 'city-state': 'Sprague River, OR', 'county': 'Klamath'}
{'_id': ObjectId('5e1a2fff0fa58fe64d04a7eb'), 'city-state/county': 'Summer Lake, OR/Lake', 'city-state': 'Summer Lake, OR', 'county': 'Lake'}
{'_id': Ob